In [ ]:
# 导包
import pandas as pd
import json
import os
import sqlite3
import h5py
import numpy as np


In [3]:
course_data = []
user_data = []
with open("../data/MOOCCube/entities/course.json", "r", encoding="utf-8") as f1:
    for line_num, line in enumerate(f1, 1):
        line = line.strip()
        data = json.loads(line)
        course_data.append(data)
print(f"成功解析了 {len(course_data)} 条课程数据")

with open("../data/MOOCCube/entities/user.json", "r", encoding='utf-8') as f2:
    for line_num, line in enumerate(f2, 1):
        line = line.strip()
        data = json.loads(line)
        user_data.append(data)
print(f"成功解析了 {len(user_data)} 条用户数据")
# ID映射
item_id_map = {}
user_id_map = {}
course_info = {}
user_info = {}
for course in course_data:
    course_id = course['id']
    course_name = course['name']
    course_about = course['about']
    if course_id not in item_id_map:
        item_id_map[course_id] = len(item_id_map) + 1 # (item_id, course_name, course_about)
        course_info[course_id] = (course_name, course_about)

for user in user_data:
    user_id = user['id']
    user_name = user['name']
    user_interact = user['course_order']
    if user_id not in user_id_map:
        user_id_map[user_id] = len(user_id_map) + 1 # (user_id, user_name, user_interact)
        user_info[user_id] = (user_name, user_interact)



成功解析了 706 条课程数据
成功解析了 199199 条用户数据


In [4]:
user_info

{'U_7001215': ('李喜锋',
  ['C_course-v1:TsinghuaX+00740043_2x_2015_T2+sp',
   'C_course-v1:TsinghuaX+30240184+sp',
   'C_course-v1:TsinghuaX+00740043X_2015_T2+sp',
   'C_course-v1:TsinghuaX+10421094X_2015_2+sp',
   'C_course-v1:TsinghuaX+30240184_2X+sp']),
 'U_10402446': ('五元香',
  ['C_course-v1:TsinghuaX+00510888X+2019_T1',
   'C_course-v1:TsinghuaX+30640014X+sp']),
 'U_10359065': ('魏珊',
  ['C_course-v1:TsinghuaX+00612642X+sp',
   'C_course-v1:TsinghuaX+80000271X+sp']),
 'U_7423998': ('郭海滨',
  ['C_course-v1:TsinghuaX+30240184_2X+sp',
   'C_course-v1:SCUT+145033+sp',
   'C_course-v1:TsinghuaX+00740043X_2015_T2+sp',
   'C_course-v1:TsinghuaX+30240184+sp',
   'C_course-v1:TsinghuaX+30640014X+sp',
   'C_course-v1:TsinghuaX+00690092X+sp',
   'C_course-v1:TsinghuaX+30240243X+sp']),
 'U_545306': ('李其艳',
  ['C_course-v1:TsinghuaX+20430064_2X+sp',
   'C_course-v1:TsinghuaX+02070251X+2019_T1',
   'C_course-v1:TsinghuaX+0350161X_2015_T2+sp',
   'C_course-v1:TsinghuaX+60240013X+sp',
   'C_course-v1:

In [14]:
user_id_map

{'U_7001215': np.int32(1),
 'U_10402446': np.int32(2),
 'U_10359065': np.int32(3),
 'U_7423998': np.int32(4),
 'U_545306': np.int32(5),
 'U_7594101': np.int32(6),
 'U_10783393': np.int32(7),
 'U_7594103': np.int32(8),
 'U_1201914': np.int32(9),
 'U_9846519': np.int32(10),
 'U_6066001': np.int32(11),
 'U_2993044': np.int32(12),
 'U_9538387': np.int32(13),
 'U_3234246': np.int32(14),
 'U_3234249': np.int32(15),
 'U_10404869': np.int32(16),
 'U_7193771': np.int32(17),
 'U_7193778': np.int32(18),
 'U_10777930': np.int32(19),
 'U_9364708': np.int32(20),
 'U_10116049': np.int32(21),
 'U_8453059': np.int32(22),
 'U_10699718': np.int32(23),
 'U_8824953': np.int32(24),
 'U_8824957': np.int32(25),
 'U_8824959': np.int32(26),
 'U_8824958': np.int32(27),
 'U_484201': np.int32(28),
 'U_9658483': np.int32(29),
 'U_9910483': np.int32(30),
 'U_8261884': np.int32(31),
 'U_6978915': np.int32(32),
 'U_11628214': np.int32(33),
 'U_5305505': np.int32(34),
 'U_11577686': np.int32(35),
 'U_7726028': np.int32

In [6]:
# 用户-项目交互数据
user_item_interact = []
for user_id, user_profile in user_info.items():
    user_name = user_profile[0]
    item_list = user_profile[1]
    item_id_list = []
    for item in item_list:
        item_id_list.append(item_id_map[item])
    user_item_interact.append((user_id_map[user_id], user_name, item_id_list))

user_item_interact

[(1, '李喜锋', [29, 63, 28, 52, 66]),
 (2, '五元香', [470, 140]),
 (3, '魏珊', [8, 190]),
 (4, '郭海滨', [66, 243, 28, 63, 140, 25, 67]),
 (5, '李其艳', [93, 492, 47, 72, 107, 50, 405, 167, 42, 27]),
 (6, '侨英喆', [70, 84]),
 (7, '藤雁玉', [217, 405, 179, 581]),
 (8, '巴鹏', [63, 28, 100, 77, 29, 73]),
 (9, '辛元龙', [36, 32, 83]),
 (10, '占澹', [164, 100, 67, 273]),
 (11, '谢厚', [84, 70]),
 (12, '程贝', [63, 36]),
 (13, '刘文满', [140, 63, 100, 356]),
 (14, '称语山', [100, 188, 58, 21, 28]),
 (15, '董振霞', [485, 152, 368, 50, 140, 119, 358, 187, 8]),
 (16, '东郭醉柳', [153, 123]),
 (17, '阙俊语', [67, 104]),
 (18, '义伟泽', [58, 100]),
 (19, '闵安歌', [153, 358]),
 (20, '韩兆德', [555, 560, 556, 552, 80]),
 (21, '廖梦阳', [217, 652, 50]),
 (22, '运嘉胜', [136, 24]),
 (23, '张廖夜玉', [8, 152]),
 (24, '官敏华', [143, 7]),
 (25, '林幼', [164, 140]),
 (26, '展德华', [152, 23]),
 (27, '林铭述', [63, 67]),
 (28, '公羊碧彤', [17, 5]),
 (29, '金日正', [63, 96]),
 (30, '沈恨寒', [477, 80]),
 (31, '洋涵润', [120, 8, 156]),
 (32, '悉和宜', [156, 251, 96, 172, 357, 479]),
 (33, '蒙子真'

In [7]:
# 统计 user_item_interact 中历史序列长度
seq_lens = [len(x[2]) for x in user_item_interact]
print('num_users:', len(seq_lens))
print('max_seq_len:', max(seq_lens) if seq_lens else 0)
print('min_seq_len:', min(seq_lens) if seq_lens else 0)
print('mean_seq_len:', float(np.mean(seq_lens)) if seq_lens else 0.0)
for p in [50, 90, 95, 99]:
    print(f'p{p}_seq_len:', int(np.percentile(seq_lens, p)) if seq_lens else 0)


num_users: 199199
max_seq_len: 161
min_seq_len: 2
mean_seq_len: 3.4274921058840655
p50_seq_len: 2
p90_seq_len: 6
p95_seq_len: 8
p99_seq_len: 15


In [8]:
# 存储数据
with h5py.File('../data/user_item_interact.h5', 'w') as f:
    # 提取键和值
    user_num_id = [item[0] for item in user_item_interact]
    user_name = [item[1] for item in user_item_interact]
    values = [item[2] for item in user_item_interact]
    
    # 存储键数组
    f.create_dataset('user_id', data=user_num_id, dtype='int32')
    dt_vlen = h5py.special_dtype(vlen=str)  # 变长字符串类型
    dset_name = f.create_dataset('user_profile', (len(user_name),), dtype=dt_vlen)
    for i, key in enumerate(user_name):
        dset_name[i] = key
    dt = h5py.special_dtype(vlen=np.dtype('int32'))
    dset = f.create_dataset('item_id_list', (len(values),), dtype=dt)
    for i, val in enumerate(values):
        dset[i] = val
    
    # 添加属性说明
    f.attrs['description'] = '键值对数据，keys是键，values是变长数组'
    f.attrs['num_items'] = len(data)

In [9]:
# 生成h5文件
with h5py.File('../data/course_id_map.h5', 'w') as f:
     # 提取键和值
    keys = list(item_id_map.keys())
    values = list(item_id_map.values())
    dt_vlen = h5py.special_dtype(vlen=str)  # 变长字符串类型
    dset_keys = f.create_dataset('item_id', (len(keys),), dtype=dt_vlen)
    for i, key in enumerate(keys):
        dset_keys[i] = key
    # 值存储为整数
    f.create_dataset('item_num_id', data=values, dtype='int32')

with h5py.File('../data/user_id_map.h5', 'w') as f:
     # 提取键和值
    keys = list(user_id_map.keys())
    values = list(user_id_map.values())
    dt_vlen = h5py.special_dtype(vlen=str)  # 变长字符串类型
    dset_keys = f.create_dataset('user_id', (len(keys),), dtype=dt_vlen)
    for i, key in enumerate(keys):
        dset_keys[i] = key
    # 值存储为整数
    f.create_dataset('user_num_id', data=values, dtype='int32')

with h5py.File('../data/course_info.h5', 'w') as f:
     # 提取键和值
    course_id = list(course_info.keys())
    course_name = []
    item_info = []
    for keys, (name, info) in course_info.items():
        course_name.append(name)
        item_info.append(info)
    dt_vlen = h5py.special_dtype(vlen=str)  # 变长字符串类型
    dset_keys = f.create_dataset('item_id', (len(course_id),), dtype=dt_vlen)
    for i, key in enumerate(course_id):
        dset_keys[i] = key
    # 值存储为整数
    dset_info = f.create_dataset('item_info', (len(item_info),), dtype=dt_vlen)
    for i, values in enumerate(item_info):
        dset_info[i] = values
    dset_name = f.create_dataset('item_name', (len(course_name),), dtype=dt_vlen)
    for i, values in enumerate(course_name):
        dset_name[i] = values
    

In [10]:
course_info

{'C_course-v1:McGillX+ATOC185x+2015_T1': ('自然灾害（自主模式）',
  '<p>地球上没有一处地方不发生自然灾害。当我们以科学的眼光看待这些自然灾害的原因和本质时，我们可以更好地减轻灾难的后果。然而，随着世界人口持续增长，越来越多的人受到灾害的威胁。本门课程将探索不同类型自然灾害背后的科学原理，以及人类在控制、预测这些灾害方面的可为与不可为。学完课程后，学生可以深入理解自然灾害，而不仅仅是停留在新闻标题的了解。同时，还将学到减小自然灾害影响的方式。</p><p>每一个人都应该理解自然灾害发生的科学原理。城市规划者需要知道房屋建造的合适位置。政治家需要做出科学合理的决策。紧急管理官员需要知道潜在灾难的本质，以及预防灾难的方式。记者则需要科学准确地进行报导。</p><p>你将学到：</p><p>● 探讨人类与自然之间的矛盾</p><p>● 探讨自然灾害对全球的影响和它们之间的联系</p><p>● 探讨自然灾害发生的科学原理</p>'),
 'C_course-v1:TsinghuaX+THESIS2015X+2015_T1': ('2015年清华大学研究生学位论文答辩（二）',
  '<p>学位论文答辩环节是研究生培养的重要环节，为了充分发挥该环节的育人作用，搭建学术交流的平台，进一步保障和提高研究生培养质量，清华大学研究生院从2014年开始，从申请学位的博士、硕士研究生中选取了部分具有代表性的学位论文答辩进行录像，并首次将答辩视频上传学堂在线，获得了社会各界的认可和积极反响。</p><p>2015年，清华大学将继续这一形式，遴选不同专业的博士、硕士研究生的学位论文答辩视频，继续以MOOC形式共享呈现给大家，以使更多的人能够分享这些资源，搭建更为广阔的学术交流平台。</p><p>如果这些视频能对您的学术研究有所帮助和启发，则是我们十分期待并愿意看到的事。</p>'),
 'C_course-v1:TsinghuaX+THESIS2014_1X_tv+_2014_': ('2014年清华大学研究生学位论文答辩（一）',
  '<p>学位论文答辩环节是研究生培养的重要环节，为了充分发挥该环节的育人作用，搭建学术交流的平台，进一步保障和提高研究生培养质量，清华大学研究生院从2014年春季学期申请学位的博士、硕士研究生中选取了部分具有

In [ ]:
rec_data = []
with h5py.File('../data/user_item_interact.h5', 'r') as f1:
    user_ids = f1['user_id'][:]          # 提取所有 user_id
    user_profile = f1['user_profile'].asstr(encoding='utf-8')[:] # 提取所有 user_profile
    item_lists = f1['item_id_list'][:]    # 提取所有变长数组
    rec_data = list(zip(user_ids, user_profile, item_lists))
print(rec_data[:5])

item_data = []
with h5py.File('../data/course_info.h5', 'r') as f2:
    item_ids = f2['item_id'].asstr(encoding='utf-8')[:]        # 提取所有 user_id
    item_name = f2['item_name'].asstr(encoding='utf-8')[:]
    item_info = f2['item_info'].asstr(encoding='utf-8')[:]  # 提取所有变长数组
    item_data = list(zip(item_ids, item_name, item_info))
print(item_data[:5])

course_id_map = {}
with h5py.File('../data/course_id_map.h5', 'r') as f3:
    course_id = f3['item_id'].asstr(encoding='utf-8')[:]
    course_num_id = f3['item_num_id'][:]
    course_id_map = dict(zip(course_id, course_num_id))
print(course_id_map)

user_id_map = {}
with h5py.File('../data/user_id_map.h5', 'r') as f4:
    user_id = f4['user_id'].asstr(encoding='utf-8')[:]
    user_num_id = f4['user_num_id'][:]
    user_id_map = dict(zip(user_id, user_num_id))
print(user_id_map)

[(np.int32(1), '李喜锋', array([29, 63, 28, 52, 66], dtype=int32)), (np.int32(2), '五元香', array([470, 140], dtype=int32)), (np.int32(3), '魏珊', array([  8, 190], dtype=int32)), (np.int32(4), '郭海滨', array([ 66, 243,  28,  63, 140,  25,  67], dtype=int32)), (np.int32(5), '李其艳', array([ 93, 492,  47,  72, 107,  50, 405, 167,  42,  27], dtype=int32))]
[('C_course-v1:McGillX+ATOC185x+2015_T1', '自然灾害（自主模式）', '<p>地球上没有一处地方不发生自然灾害。当我们以科学的眼光看待这些自然灾害的原因和本质时，我们可以更好地减轻灾难的后果。然而，随着世界人口持续增长，越来越多的人受到灾害的威胁。本门课程将探索不同类型自然灾害背后的科学原理，以及人类在控制、预测这些灾害方面的可为与不可为。学完课程后，学生可以深入理解自然灾害，而不仅仅是停留在新闻标题的了解。同时，还将学到减小自然灾害影响的方式。</p><p>每一个人都应该理解自然灾害发生的科学原理。城市规划者需要知道房屋建造的合适位置。政治家需要做出科学合理的决策。紧急管理官员需要知道潜在灾难的本质，以及预防灾难的方式。记者则需要科学准确地进行报导。</p><p>你将学到：</p><p>● 探讨人类与自然之间的矛盾</p><p>● 探讨自然灾害对全球的影响和它们之间的联系</p><p>● 探讨自然灾害发生的科学原理</p>'), ('C_course-v1:TsinghuaX+THESIS2015X+2015_T1', '2015年清华大学研究生学位论文答辩（二）', '<p>学位论文答辩环节是研究生培养的重要环节，为了充分发挥该环节的育人作用，搭建学术交流的平台，进一步保障和提高研究生培养质量，清华大学研究生院从2014年开始，从申请学位的博士、硕士研究生中选取了部分具有代表性的学位论文答辩进行录像，并首次将答辩视频上传学堂在线，获得了社会各界

In [6]:
import torch
print(torch.cuda.is_available())
print(torch.__version__)

True
2.6.0+cu124


{'U_7001215': np.int32(1), 'U_10402446': np.int32(2), 'U_10359065': np.int32(3), 'U_7423998': np.int32(4), 'U_545306': np.int32(5), 'U_7594101': np.int32(6), 'U_10783393': np.int32(7), 'U_7594103': np.int32(8), 'U_1201914': np.int32(9), 'U_9846519': np.int32(10), 'U_6066001': np.int32(11), 'U_2993044': np.int32(12), 'U_9538387': np.int32(13), 'U_3234246': np.int32(14), 'U_3234249': np.int32(15), 'U_10404869': np.int32(16), 'U_7193771': np.int32(17), 'U_7193778': np.int32(18), 'U_10777930': np.int32(19), 'U_9364708': np.int32(20), 'U_10116049': np.int32(21), 'U_8453059': np.int32(22), 'U_10699718': np.int32(23), 'U_8824953': np.int32(24), 'U_8824957': np.int32(25), 'U_8824959': np.int32(26), 'U_8824958': np.int32(27), 'U_484201': np.int32(28), 'U_9658483': np.int32(29), 'U_9910483': np.int32(30), 'U_8261884': np.int32(31), 'U_6978915': np.int32(32), 'U_11628214': np.int32(33), 'U_5305505': np.int32(34), 'U_11577686': np.int32(35), 'U_7726028': np.int32(36), 'U_7834216': np.int32(37), 'U